In [109]:
import pandas as  pd
from datetime import datetime as dt, timedelta

import plotly.express as px
import plotly.graph_objects as go
import plotly.colors 


import sys, subprocess
import plotly.io as pio
import nbformat, IPython








In [110]:
data = pd.read_csv("/Users/jasminetaha/Downloads/data.csv",low_memory=False)
data.head()

Unnamed: 0             Order id        Date                        Status  \
0           1  171-9198151-1101146  2022-04-30  Shipped - Delivered to Buyer   
1           2  404-0687676-7273146  2022-04-30                       Shipped   
2           4  407-1069790-7240320  2022-04-30                       Shipped   
3           5  404-1490984-4578765  2022-04-30                       Shipped   
4           6  408-5748499-6859555  2022-04-30                       Shipped   

  Fulfilment Ship-service-level  Qty Currency  Amount    Ship-city  Revenue  \
0   Merchant           Standard    1      INR   406.0    BENGALURU    406.0   
1     Amazon          Expedited    1      INR   329.0  NAVI MUMBAI    329.0   
2     Amazon          Expedited    1      INR   574.0      CHENNAI    574.0   
3     Amazon          Expedited    1      INR   824.0    GHAZIABAD    824.0   
4     Amazon          Expedited    1      INR   653.0   CHANDIGARH    653.0   

   Year Month_name  
0  2022      April  
1  2022      April  
2  2022      April  
3  2022      April  
4  2022      April

In [111]:
data.rename(columns={"Unnamed: 0": "CustomerID"}, inplace = True)

In [112]:
data["Date"]= pd.to_datetime(data["Date"])
data

CustomerID             Order id       Date  \
0                1  171-9198151-1101146 2022-04-30   
1                2  404-0687676-7273146 2022-04-30   
2                4  407-1069790-7240320 2022-04-30   
3                5  404-1490984-4578765 2022-04-30   
4                6  408-5748499-6859555 2022-04-30   
...            ...                  ...        ...   
110383      128970  406-6001380-7673107 2022-05-31   
110384      128971  402-9551604-7544318 2022-05-31   
110385      128972  407-9547469-3152358 2022-05-31   
110386      128973  402-6184140-0545956 2022-05-31   
110387      128974  408-7436540-8728312 2022-05-31   

                              Status Fulfilment Ship-service-level  Qty  \
0       Shipped - Delivered to Buyer   Merchant           Standard    1   
1                            Shipped     Amazon          Expedited    1   
2                            Shipped     Amazon          Expedited    1   
3                            Shipped     Amazon          Expedited    1   
4                            Shipped     Amazon          Expedited    1   
...                              ...        ...                ...  ...   
110383                       Shipped     Amazon          Expedited    1   
110384                       Shipped     Amazon          Expedited    1   
110385                       Shipped     Amazon          Expedited    1   
110386                       Shipped     Amazon          Expedited    1   
110387                       Shipped     Amazon          Expedited    1   

       Currency  Amount    Ship-city  Revenue  Year Month_name  
0           INR   406.0    BENGALURU    406.0  2022      April  
1           INR   329.0  NAVI MUMBAI    329.0  2022      April  
2           INR   574.0      CHENNAI    574.0  2022      April  
3           INR   824.0    GHAZIABAD    824.0  2022      April  
4           INR   653.0   CHANDIGARH    653.0  2022      April  
...         ...     ...          ...      ...   ...        ...  
110383      INR   517.0    HYDERABAD    517.0  2022        May  
110384      INR   999.0     GURUGRAM    999.0  2022        May  
110385      INR   690.0    HYDERABAD    690.0  2022        May  
110386      INR  1199.0        Halol   1199.0  2022        May  
110387      INR   696.0       Raipur    696.0  2022        May  

[110388 rows x 13 columns]

In [113]:
reference_date = pd.Timestamp(dt.now().date())

In [114]:
reference_date = data["Date"].max() + timedelta(days=1)
reference_date

Timestamp('2022-06-30 00:00:00')

In [115]:
rfm = data.groupby("CustomerID").agg({
    "Date": lambda x: (reference_date-x.max()).days,
    "Order id": "nunique",
    "Amount": "sum"
    
})

In [116]:
rfm.rename(columns={"Date": "Recency","Order id":"Frequency","Amount": "Value"},inplace=True)
rfm.rename(columns={"Recurrency":"Recency"})
rfm

Recency  Frequency   Value
CustomerID                            
1                61          1   406.0
2                61          1   329.0
4                61          1   574.0
5                61          1   824.0
6                61          1   653.0
...             ...        ...     ...
128970           30          1   517.0
128971           30          1   999.0
128972           30          1   690.0
128973           30          1  1199.0
128974           30          1   696.0

[110388 rows x 3 columns]

In [117]:
rfm.rename(columns={"Recurrency":"Recency"},inplace=True)

In [118]:
#defining the quantiles
quantiles = rfm.quantile(q=[0.25,0.5,0.75])

#assign rfm scores
def RScore(x,p,d):
    if p == "Recency":
        if x <= d[p][0.25]:
            return 4
        elif x <= d[p][0.5]:
            return 3
        elif x<=d[p][0.75]:
            return 2
        else: 
            return 1
    else:
        if x<= d[p][0.25]:
            return 1
        elif x<=d[p][0.5]:
            return 2
        elif x<= d[p][0.75]:
            return 3
        else:
            return 4
        
rfm["R"]= rfm["Recency"].apply(RScore, args=("Recency", quantiles))
rfm["F"]= rfm["Frequency"].apply(RScore, args = ("Frequency",quantiles))
rfm["M"]= rfm["Value"].apply(RScore, args = ("Value", quantiles))
rfm.head()

Recency  Frequency  Value  R  F  M
CustomerID                                    
1                61          1  406.0  2  1  1
2                61          1  329.0  2  1  1
4                61          1  574.0  2  1  2
5                61          1  824.0  2  1  4
6                61          1  653.0  2  1  3

In [119]:
rfm["RFM_segment"]= rfm["R"].astype(str) + rfm["F"].astype(str)+rfm["M"].astype(str)
rfm["RFM_Score"]= rfm[["R","F","M"]].sum(axis= 1)
rfm.head()

Recency  Frequency  Value  R  F  M RFM_segment  RFM_Score
CustomerID                                                           
1                61          1  406.0  2  1  1         211          4
2                61          1  329.0  2  1  1         211          4
4                61          1  574.0  2  1  2         212          5
5                61          1  824.0  2  1  4         214          7
6                61          1  653.0  2  1  3         213          6

In [120]:
segment_labels= ["Low-Value","Mid-Value","High-Value"]
def assign_segment(score):
    if score<5:
        return "Low-Value"
    elif score<9:
        return "Mid-Value"
    else:
        return "High-Value"
    
    

rfm = rfm.loc[:, ~rfm.columns.duplicated()]
rfm["RFM_Segment_Labels"] = rfm["RFM_Score"].apply(assign_segment)

rfm.head()

Recency  Frequency  Value  R  F  M RFM_segment  RFM_Score  \
CustomerID                                                              
1                61          1  406.0  2  1  1         211          4   
2                61          1  329.0  2  1  1         211          4   
4                61          1  574.0  2  1  2         212          5   
5                61          1  824.0  2  1  4         214          7   
6                61          1  653.0  2  1  3         213          6   

           RFM_Segment_Labels  
CustomerID                     
1                   Low-Value  
2                   Low-Value  
4                   Mid-Value  
5                   Mid-Value  
6                   Mid-Value

In [121]:
segment_counts = rfm["RFM_Segment_Labels"].value_counts().reset_index()
segment_counts.columns = ["RFM_segment","Count"]
segment_counts= segment_counts.sort_values("RFM_segment")


In [123]:
#create bar chart
fig = px.bar(
    segment_counts,
    x="RFM_segment",
    y="Count",
    title="Customer Distribution by RFM Segment",
    labels={"RFM_segment": "RFM Segment", "Count": "Number of Customers"},
    color="RFM_segment",
    color_discrete_sequence=px.colors.qualitative.Pastel
)


In [124]:
rfm["RFM_customer_segment"] = ''
rfm.loc[rfm["RFM_Score"]>=9, "RFM_customer_segment"] = "Best/Loyal Customers"
rfm.loc[(rfm["RFM_Score"]>=6) & (rfm["RFM_Score"]<9), "RFM_customer_segment"] = "Potential Loyal Customers"
rfm.loc[(rfm["RFM_Score"]>=5) & (rfm["RFM_Score"]<6), "RFM_customer_segment"] = "At Risk Customers"
rfm.loc[(rfm["RFM_Score"]>=4) & (rfm["RFM_Score"]<5), "RFM_customer_segment"] = "Can't Lose Customers"
rfm.loc[(rfm["RFM_Score"]>=3)&(rfm["RFM_Score"]<4), "RFM_customer_segment"] = "Lost Customers"
segment_counts = rfm["RFM_customer_segment"].value_counts().reset_index()



In [126]:
segment_product_counts = rfm.groupby(["RFM_Segment_Labels","RFM_customer_segment"]).size().reset_index(name ="Count")
segment_product_counts= segment_product_counts.sort_values(by= "Count", ascending=False)

In [129]:
#creating the treemap
fig_treemap_seg_product = px.treemap(
    segment_product_counts,
    path=["RFM_Segment_Labels","RFM_customer_segment"],
    values="Count",
    color = "RFM_Segment_Labels",
    color_discrete_sequence= px.colors.qualitative.Pastel_r,
    title="RFM Customer Segments by Value")
fig_treemap_seg_product.show()







In [130]:
vip_segment = rfm[rfm["RFM_customer_segment"]=="Best/Loyal Customers"]

In [131]:
fig = go.Figure()
fig.add_trace(go.Box(y=vip_segment["Recency"], name ="Recency"))
fig.add_trace(go.Box(y=vip_segment["Frequency"], name ="Frequency"))
fig.add_trace(go.Box(y=vip_segment["Value"], name ="Monetary Value"))

In [132]:
correlation_matrix = vip_segment[["R","F","M"]].corr()
correlation_matrix
rfm[["Recency", "Frequency", "Value"]].nunique()



Recency       91
Frequency      1
Value        862
dtype: int64

In [133]:

fig = px.histogram(
    rfm,
    x="Value",
    nbins=30,
    title="Distribution of Customer Spend",
    labels={"Value": "Total Spend per Customer"},
    opacity=0.85
)




fig.show()

In [ ]:

rfm_pos = rfm[rfm["Value"] > 0]

fig = px.histogram(
    rfm_pos,
    x="Value",
    nbins=40,
    title="Distribution of Customer Spend (Log Scale)",
    labels={"Value": "Total Spend per Customer"},
    opacity=0.9
)

fig.update_layout(
    template="simple_white",
    title=dict(x=0.5),
    xaxis=dict(type="log", title="Total Spend (log scale)"),
    yaxis=dict(title="Number of Customers"),
    bargap=0.02
)

fig.show()


In [137]:
import numpy as np
import plotly.express as px

rfm["log_value"] = np.log1p(rfm["Value"])

fig = px.histogram(
    rfm,
    x="log_value",
    nbins=25,   # fewer bins = smoother for discrete values
    title="Distribution of Customer Spend",
    labels={"log_value": "log(1 + Total Spend)"},
    opacity=0.9
)

fig.update_layout(
    template="simple_white",
    title=dict(x=0.5),
    xaxis_title="log(1 + Total Spend)",
    yaxis_title="Number of Customers",
    bargap=0.05,
    font=dict(size=13)
)

fig.show()


In [138]:
import pandas as pd

bins = [0, 300, 500, 700, 1000, 2000, 6000]
labels = [
    "< 300",
    "300–500",
    "500–700",
    "700–1k",
    "1k–2k",
    "2k+"
]

rfm["Spend_Bucket"] = pd.cut(
    rfm["Value"],
    bins=bins,
    labels=labels,
    right=False
)
bucket_counts = (
    rfm["Spend_Bucket"]
    .value_counts()
    .sort_index()
    .reset_index()
)

bucket_counts.columns = ["Spend Range", "Number of Customers"]


In [139]:
fig = px.bar(
    bucket_counts,
    x="Spend Range",
    y="Number of Customers",
    title="Customer Spend Distribution",
    text="Number of Customers"
)

fig.update_layout(
    template="simple_white",
    title=dict(x=0.5),
    xaxis_title="Total Spend per Customer",
    yaxis_title="Number of Customers",
    font=dict(size=13)
)

fig.update_traces(
    textposition="outside",
    marker_line_width=1
)

fig.show()

In [140]:
segment_counts = rfm["RFM_Segment_Labels"].value_counts()
import plotly.graph_objects as go
import plotly.colors as pc

pastel_colors = pc.qualitative.Pastel

highlight_segment = "High-Value"  # change if needed
highlight_color = "rgb(158, 202, 225)"

bar_colors = [
    highlight_color if segment == highlight_segment 
    else pastel_colors[i % len(pastel_colors)]
    for i, segment in enumerate(segment_counts.index)
]


In [141]:
fig = go.Figure(
    data=[
        go.Bar(
            x=segment_counts.index,
            y=segment_counts.values,
            marker=dict(
                color=bar_colors,
                line=dict(color="white", width=1.5)
            ),
            opacity=0.85
        )
    ]
)

fig.update_layout(
    template="simple_white",
    title=dict(
        text="Customer Distribution by RFM Segment",
        x=0.5
    ),
    xaxis_title="Customer Type",
    yaxis_title="Number of Customers",
    showlegend=False,
    font=dict(size=13)
)

fig.show()


In [ ]:
import plotly.graph_objects as go
import plotly.colors as pc


segment_counts = rfm["RFM_customer_segment"].value_counts()
pastel_colors = pc.qualitative.Pastel
highlight_segment = "Best/Loyal Customers"
highlight_color = "rgb(158, 202, 225)"  
bar_colors = [
    highlight_color if segment == highlight_segment
    else pastel_colors[i % len(pastel_colors)]
    for i, segment in enumerate(segment_counts.index)
]


fig = go.Figure(
    data=[
        go.Bar(
            x=segment_counts.index,
            y=segment_counts.values,
            marker=dict(
                color=bar_colors,
                line=dict(color="rgb(8, 48, 107)", width=1.5)
            ),
            opacity=0.6
        )
    ]
)

fig.update_layout(
    title=dict(
        text="Customer Distribution by RFM Segments",
        x=0.5
    ),
    xaxis_title="RFM Segments",
    yaxis_title="Number of Customers",
    showlegend=False,
  

    font=dict(size=13)
)

fig.show()


In [ ]:
import plotly.graph_objects as go
segment_scores = (
    rfm
    .groupby("RFM_customer_segment")[["R", "F", "M"]]
    .mean()
    .reset_index()
)

fig = go.Figure()
# Recency bar
fig.add_trace(
    go.Bar(
        x=segment_scores["RFM_customer_segment"],
        y=segment_scores["R"],
        name="Recency Score",
        marker_color="rgb(158, 202, 225)"
    )
)

# Frequency bar
fig.add_trace(
    go.Bar(
        x=segment_scores["RFM_customer_segment"],
        y=segment_scores["F"],
        name="Frequency Score",
        marker_color="rgb(94, 158, 217)"
    )
)

# Monetary bar
fig.add_trace(
    go.Bar(
        x=segment_scores["RFM_customer_segment"],
        y=segment_scores["M"],
        name="Monetary Score",
        marker_color="rgb(32, 102, 148)"
    )
)

fig.update_layout(
    title="Comparison of RFM Segments based on Recency, Frequency, and Monetary Scores",
    xaxis_title="RFM Segments",
    yaxis_title="Score",
    barmode="group",
    
   
)

fig.show()


In [144]:
rfm.drop(columns=["log_value","Spend_Bucket"], inplace=True)


In [145]:
rfm.to_csv("rfm_customer_segments1.csv", index=False)


In [158]:
rfm.drop(columns=["CustomerID","level_0"], inplace=True)

In [162]:
rfm.index = range(1, len(rfm) + 1)
rfm.index.name = "CustomerID"

rfm.head()

Recency  Frequency  Value  R  F  M RFM_segment  RFM_Score  \
CustomerID                                                              
1                61          1  406.0  2  1  1         211          4   
2                61          1  329.0  2  1  1         211          4   
3                61          1  574.0  2  1  2         212          5   
4                61          1  824.0  2  1  4         214          7   
5                61          1  653.0  2  1  3         213          6   

           RFM_Segment_Labels       RFM_customer_segment  
CustomerID                                                
1                   Low-Value       Can't Lose Customers  
2                   Low-Value       Can't Lose Customers  
3                   Mid-Value          At Risk Customers  
4                   Mid-Value  Potential Loyal Customers  
5                   Mid-Value  Potential Loyal Customers

In [167]:
rfm.to_csv("final_rfm_customer_segments1.csv")

In [ ]:
rfm = rfm.reset_index()
rfm.head()  
rfm.rename(columns={"index": "CustomerID"}, inplace=True)
rfm.drop_duplicates(inplace=True)
rfm.head()


CustomerID  CustomerID  level_0  CustomerID  CustomerID  Recency  \
0           0           0        0           0           1       61   
1           1           1        1           1           2       61   
2           2           2        2           2           4       61   
3           3           3        3           3           5       61   
4           4           4        4           4           6       61   

   Frequency  Value  R  F  M RFM_segment  RFM_Score RFM_Segment_Labels  \
0          1  406.0  2  1  1         211          4          Low-Value   
1          1  329.0  2  1  1         211          4          Low-Value   
2          1  574.0  2  1  2         212          5          Mid-Value   
3          1  824.0  2  1  4         214          7          Mid-Value   
4          1  653.0  2  1  3         213          6          Mid-Value   

        RFM_customer_segment  
0       Can't Lose Customers  
1       Can't Lose Customers  
2          At Risk Customers  
3  Potential Loyal Customers  
4  Potential Loyal Customers

In [168]:
segment_summary = (
    rfm.groupby("RFM_customer_segment")
    .agg(
        Customers=("Value", "count"),
        Customer_Percent=("Value", lambda x: round(len(x) / len(rfm) * 100, 2)),
        Total_Revenue=("Value", "sum"),
        Avg_Revenue=("Value", "mean"),
        Avg_Frequency=("Frequency", "mean"),
        Avg_Recency=("Recency", "mean")
    )
    .reset_index()
    .sort_values("Total_Revenue", ascending=False)
)

segment_summary


RFM_customer_segment  Customers  Customer_Percent  Total_Revenue  \
4  Potential Loyal Customers      61172             55.42     44576114.0   
0          At Risk Customers      19764             17.90     10414933.0   
1       Best/Loyal Customers       7359              6.67      7729018.0   
2       Can't Lose Customers      14568             13.20      6281511.0   
3             Lost Customers       7525              6.82      2655177.0   

   Avg_Revenue  Avg_Frequency  Avg_Recency  
4   728.701269            1.0    39.028036  
0   526.964835            1.0    61.184780  
1  1050.281016            1.0    14.279522  
2   431.185544            1.0    71.069811  
3   352.847442            1.0    80.692359

insight #1: Best customers represent a small portion of the customers. Only about 6.67% of the customers base generate ~77.2M in revunue and have the highest overall revenue per customer. This means losing them would severely impact revenue 

insight #2: 55.42 % of the customer base are Potential loyal customers which generate the highest revenue, indicating strong engagement but untapped loyalty. 

insight #3: At Risk and Can’t Lose Customers together represent 31% of customers and contribute over 16M in historical revenue, but show long inactivity periods. This means theres a high-value churn risk 

insight #4: lost customers have the highest recency average and lowest revenue, indicating complete disengagement. retention weakness is evident

insight #5: The average frequency for all customer segments is 1.0, meaning the dataset only includes/reflects single-purchase customers.

In [169]:
strategy_table = pd.DataFrame({
    "RFM_customer_segment": [
        "Best/Loyal Customers",
        "Potential Loyal Customers",
        "At Risk Customers",
        "Can't Lose Customers",
        "Lost Customers"
    ],
    "Recommended_Strategy": [
        "VIP rewards, early access, exclusive offers",
        "Loyalty programs, reminders, frequency incentives",
        "Win-back campaigns, limited-time discounts",
        "Personalized reactivation, high-touch outreach",
        "Low-cost reactivation or exclude from campaigns"
    ]
})

strategy_table


RFM_customer_segment  \
0       Best/Loyal Customers   
1  Potential Loyal Customers   
2          At Risk Customers   
3       Can't Lose Customers   
4             Lost Customers   

                                Recommended_Strategy  
0        VIP rewards, early access, exclusive offers  
1  Loyalty programs, reminders, frequency incentives  
2         Win-back campaigns, limited-time discounts  
3     Personalized reactivation, high-touch outreach  
4    Low-cost reactivation or exclude from campaigns

In [174]:
strategy_table.to_csv("rfm_strategy_table.csv", index=False)
